# Objectives {.unnumbered}

By the end of this lab, you will:
1. Load and analyze the **Lightcast dataset** in **Spark DataFrame**.
2. Create **five easy and three medium-complexity visualizations** using **Plotly**.
3. Explore **salary distributions, employment trends, and job postings**.
4. Analyze **skills in relation to NAICS/SOC/ONET codes and salaries**.
5. Customize **colors, fonts, and styles** in all visualizations (**default themes result in a 2.5-point deduction**).
6. Follow **best practices for reporting on data communication**.

# Step 1: Load the Dataset {.unnumbered}


In [2]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "vscode"
from pyspark.sql import SparkSession
from pyspark.sql.functions import col


# Initialize Spark Session
spark = SparkSession.builder.appName("LightcastData").getOrCreate()

# Load Data
df = spark.read.option("header", "true").option("inferSchema", "true").option("multiLine","true").option("escape", "\"").csv("./data/lightcast_job_postings.csv")

# Show Schema and Sample Data
df.printSchema()
df.show(5)


root
 |-- ID: string (nullable = true)
 |-- LAST_UPDATED_DATE: string (nullable = true)
 |-- LAST_UPDATED_TIMESTAMP: timestamp (nullable = true)
 |-- DUPLICATES: integer (nullable = true)
 |-- POSTED: string (nullable = true)
 |-- EXPIRED: string (nullable = true)
 |-- DURATION: integer (nullable = true)
 |-- SOURCE_TYPES: string (nullable = true)
 |-- SOURCES: string (nullable = true)
 |-- URL: string (nullable = true)
 |-- ACTIVE_URLS: string (nullable = true)
 |-- ACTIVE_SOURCES_INFO: string (nullable = true)
 |-- TITLE_RAW: string (nullable = true)
 |-- BODY: string (nullable = true)
 |-- MODELED_EXPIRED: string (nullable = true)
 |-- MODELED_DURATION: integer (nullable = true)
 |-- COMPANY: integer (nullable = true)
 |-- COMPANY_NAME: string (nullable = true)
 |-- COMPANY_RAW: string (nullable = true)
 |-- COMPANY_IS_STAFFING: boolean (nullable = true)
 |-- EDUCATION_LEVELS: string (nullable = true)
 |-- EDUCATION_LEVELS_NAME: string (nullable = true)
 |-- MIN_EDULEVELS: integer (

25/03/23 21:39:24 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+--------------------+-----------------+----------------------+----------+--------+---------+--------+--------------------+--------------------+--------------------+-----------+-------------------+--------------------+--------------------+---------------+----------------+--------+--------------------+-----------+-------------------+----------------+---------------------+-------------+-------------------+-------------+------------------+---------------+--------------------+--------------------+--------------------+-------------+------+-----------+----------------+-------------------+---------+-----------+--------------------+--------------------+-------------+------+--------------+-----+--------------------+-----+----------+---------------+--------------------+---------------+--------------------+------------+--------------------+------------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+------

---

# Salary Distribution by Employment Type
- Identify salary trends across different employment types.
- **Filter the dataset**
  - Remove records where **salary is missing or zero**.
- **Aggregate Data**
  - Group by **employment type** and compute salary distribution.
- **Visualize results**
  - Create a **box plot** where:
    - **X-axis** = `EMPLOYMENT_TYPE_NAME`
    - **Y-axis** = `SALARY_FROM`
  - Customize **colors, fonts, and styles** to avoid a **2.5-point deduction**.
- **Explanation:** Write two sentences about what the graph reveals.



In [8]:
# Select needed columns and convert to Pandas
pdf = df.select("EMPLOYMENT_TYPE_NAME", "SALARY").toPandas()

# box plot
fig = px.box(pdf,
             x="EMPLOYMENT_TYPE_NAME",
             y="SALARY",
             title="Salary Distribution by Employment Type",
             color_discrete_sequence=["#325A9B"],   # deep blue boxes
             width=1000,
             height=600)

# Customizing
fig.update_layout(
    font_family="Arial",
    title_font_size=16,
    plot_bgcolor="#F7E1A0",   # inner plot area
    paper_bgcolor="#F7E1A0"   # outer background area
)

fig.show()


**Interpretation**

- here our box plot shows that full-time positions (> 32 hours) have the highest median salary at approximately $116.5k, along with a wide salary range and many high outliers. 
- Part-time/full-time roles follow with a median salary of $100k, while part-time roles (< 32 hours) have the lowest median at around $86.4k. 
- So, full-time jobs have greater salary variability compared to other employment types.


---

# Salary Distribution by Industry
- Compare salary variations across industries.
- **Filter the dataset**
  - Keep records where **salary is greater than zero**.
- **Aggregate Data**
  - Group by **NAICS industry codes**.
- **Visualize results**
  - Create a **box plot** where:
    - **X-axis** = `NAICS2_NAME`
    - **Y-axis** = `SALARY_FROM`
  - Customize colors, fonts, and styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [9]:
# Filter out rows with salary <= 0
df_industry = df.filter(col("SALARY_FROM") > 0)
pdf_industry = df_industry.select("NAICS2_NAME", "SALARY_FROM").toPandas()

# Create box plot with customized background and color
fig = px.box(pdf_industry,
             x="NAICS2_NAME",
             y="SALARY_FROM",
             title="Salary Distribution by Industry",
             color_discrete_sequence=["#D62728"],  # your chosen box color
             width=1500,
             height=900)

# Apply font and background styling
fig.update_layout(
    font_family="Arial",
    title_font_size=16,
    plot_bgcolor="#F7E1A0",   # inner plot background
    paper_bgcolor="#F7E1A0"   # outer chart background
)

fig.show()


**Iinterpretation**

- Our box plot shows that industries like Administrative, Manufacturing, and Information have higher salary ranges and more outliers, indicating potential for high-paying roles. 

- In contrast, sectors such as Arts, Entertainment, and Accommodation tend to have lower and more concentrated salary distributions.


---

# Job Posting Trends Over Time
- Analyze how job postings fluctuate over time.
- **Aggregate Data**
  - Count job postings per **posted date (`POSTED`)**.
- **Visualize results**
  - Create a **line chart** where:
    - **X-axis** = `POSTED`
    - **Y-axis** = `Number of Job Postings`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [12]:
# Step 1: Group by POSTED date and count number of job postings
df_posting_trend = df.groupBy("POSTED").count().orderBy("POSTED")

# Step 2: Convert to Pandas for plotting
pdf_posting_trend = df_posting_trend.toPandas()

# Step 3: Create a line chart
import plotly.express as px

fig = px.line(pdf_posting_trend,
              x="POSTED",
              y="count",
              title="Job Posting Trends Over Time",
              markers=True,
              color_discrete_sequence=["#D62728"],  # red line
              width=1000,
              height=500)

# Customization
fig.update_layout(
    font_family="Arial",
    title_font_size=16,
    plot_bgcolor="#F7E1A0",
    paper_bgcolor="#F7E1A0",
)

fig.update_xaxes(
    tickformat="%b %d",   # e.g., May 05
    tickfont=dict(size=10),
    showgrid=False
)

fig.update_yaxes(
    title_text="Number of Job Postings",
    showgrid=True
)
fig.show()


**Interpretation**

- Job postings show frequent short-term spikes and dips, suggesting high variability in daily recruitment activity.

- Late August to mid-September shows a noticeable increase in postings, possibly due to end-of-summer hiring.

- Despite fluctuations, no long-term upward or downward trend is clearly dominant across the observed period.


---

# Top 10 Job Titles by Count
- Identify the most frequently posted job titles.
- **Aggregate Data**
  - Count the occurrences of each **job title (`TITLE_NAME`)**.
  - Select the **top 10 most frequent titles**.
- **Visualize results**
  - Create a **bar chart** where:
    - **X-axis** = `TITLE_NAME`
    - **Y-axis** = `Job Count`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [13]:
# Step 1: Group by title and count
df_titles = df.groupBy("TITLE_NAME").count().orderBy("count", ascending=False).limit(10)

# Step 2: Convert to Pandas for plotting
pdf_titles = df_titles.toPandas()

# Step 3: Create bar chart
import plotly.express as px

fig = px.bar(pdf_titles,
             x="TITLE_NAME",
             y="count",
             title="Top 10 Job Titles by Count",
             color_discrete_sequence=["#D62728"],
             width=900,
             height=500)

# Step 4: Apply custom styling
fig.update_layout(
    font_family="Arial",
    title_font_size=16,
    plot_bgcolor="#F7E1A0",
    paper_bgcolor="#F7E1A0",
    xaxis_title="Job Title",
    yaxis_title="Job Count"
)

# Optional: Rotate x-axis labels if they overlap
fig.update_xaxes(tickangle=-45)

fig.show()


**Interpretation**

- The job title **"Data Analysis"** is by far the most frequently posted role, with a significantly higher count than all others.

- Other commonly listed titles include **Business Intelligence Analyst** and **Enterprise Architect**, reflecting high demand for data and tech-related roles.

- The sharp drop after the top 2–3 titles indicates a concentrated demand for a few specific positions in the job market.


---

# Remote vs On-Site Job Postings
- Compare the proportion of remote and on-site job postings.
- **Aggregate Data**
  - Count job postings by **remote type (`REMOTE_TYPE_NAME`)**.
- **Visualize results**
  - Create a **pie chart** where:
    - **Labels** = `REMOTE_TYPE_NAME`
    - **Values** = `Job Count`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [22]:
# Step 1: Filter only relevant remote types
df_remote_filtered = df.filter(
    col("REMOTE_TYPE_NAME").isin(["Remote", "Hybrid Remote", "Not Remote"])
).groupBy("REMOTE_TYPE_NAME").count()

# Step 2: Convert to Pandas
pdf_remote_filtered = df_remote_filtered.toPandas()

# Step 3: Create pie chart
import plotly.express as px

fig = px.pie(pdf_remote_filtered,
             names="REMOTE_TYPE_NAME",
             values="count",
             title="Remote vs On-Site Job Postings",
             color_discrete_sequence=px.colors.sequential.Reds)

# Step 4: Style
fig.update_layout(
    font_family="Arial",
    title_font_size=16,
    plot_bgcolor="#F7E1A0",
    paper_bgcolor="#F7E1A0"
)

fig.show()


---

**INterpretation**

- A significant majority of job postings are classified as Remote, indicating a strong shift toward flexible work setups.

- Hybrid Remote and Not Remote roles represent a smaller share, showing that while traditional on-site roles still exist, they are far less common in the current landscape.

# Skill Demand Analysis by Industry (Stacked Bar Chart)
- Identify which skills are most in demand in various industries.
- **Aggregate Data**
  - Extract **skills** from job postings.
  - Count occurrences of skills grouped by **NAICS industry codes**.
- **Visualize results**
  - Create a **stacked bar chart** where:
    - **X-axis** = `Industry`
    - **Y-axis** = `Skill Count`
    - **Color** = `Skill`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [ ]:
# Your code for 6th question here


# Salary Analysis by ONET Occupation Type (Bubble Chart)
- Analyze how salaries differ across ONET occupation types.
- **Aggregate Data**
  - Compute **median salary** for each occupation in the **ONET taxonomy**.
- **Visualize results**
  - Create a **bubble chart** where:
    - **X-axis** = `ONET_NAME`
    - **Y-axis** = `Median Salary`
    - **Size** = Number of job postings
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [ ]:
# Your code for 7th question here

# Career Pathway Trends (Sankey Diagram)
- Visualize job transitions between different occupation levels.
- **Aggregate Data**
  - Identify career transitions between **SOC job classifications**.
- **Visualize results**
  - Create a **Sankey diagram** where:
    - **Source** = `SOC_2021_2_NAME`
    - **Target** = `SOC_2021_3_NAME`
    - **Value** = Number of transitions
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [ ]:
# Your code for 8th question here